In [1]:
%matplotlib notebook

# generic packages
import sys
import re, numpy as np, pandas as pd
from pprint import pprint
from matplotlib.ticker import PercentFormatter

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', None)
pd.set_option('display.precision', 1)

import warnings
warnings.filterwarnings("ignore")
warnings.filterwarnings("ignore", category=DeprecationWarning) 


# graphing, vis stuff
import matplotlib.pyplot as plt

# additional libraries
from collections import Counter



# 1 Region and Domain

# 2 Research Question

"Which city division in the City of Toronto spent the most money in 2021 (and how does that compare with the distribution of its approved operating budget for 2021)?"



# 3 Links

In [2]:
# competitive contracts - City of Toronto

CC_URL = "https://wx.toronto.ca/inter/pmmd/callawards.nsf/postedawards?OpenView"
CC_URL2 = "https://wx.toronto.ca/inter/pmmd/callawards.nsf/postedawards?OpenView&Start=3.8.1"

# non-competitive contracts - City of Toronto
NC_URL = "https://wx.toronto.ca/inter/pmmd/solesource.nsf/posted?OpenView&Start=1&ExpandView"
NC_URL2 = "https://wx.toronto.ca/inter/pmmd/solesource.nsf/posted?OpenView&Start=1000&ExpandView"
NC_URL3 = "https://wx.toronto.ca/inter/pmmd/solesource.nsf/posted?OpenView&Start=1999&ExpandView"



In [3]:
# WORK THROUGH ... https://realpython.com/beautiful-soup-web-scraper-python/#step-2-scrape-html-content-from-a-page

from bs4 import BeautifulSoup
import requests

urls = [CC_URL, CC_URL2, NC_URL, NC_URL2, NC_URL3]
pages = [requests.get(url) for url in urls]
soups = [BeautifulSoup(page.text, "html.parser") for page in pages]

In [4]:
tables_per_url = [soups[i].find_all('table') for i in range(len(soups))]




In [5]:
# next: try using get_tables function here: https://towardsdatascience.com/a-guide-to-scraping-html-tables-with-pandas-and-beautifulsoup-7fc24c331cf7

def get_table(table_html):
    
    rows = []
    for child in table_html.children:
        row = []
        for td in child:
            try:
                row.append(td.text.replace('\n', ''))
            except:
                continue
        if len(row) > 0:
            rows.append(row)

    df = pd.DataFrame(rows[1:], columns=rows[0])
    return df
    
ncc_dfs = [get_table(tables_per_url[i][8]) for i in range(2,5)]
ncc_all = pd.concat(ncc_dfs)

cc_dfs = [get_table(tables_per_url[i][7]) for i in range(0,2)]
cc_all = pd.concat(cc_dfs)


In [6]:
cc_money_rows = cc_all[cc_all["Contract Amount"].notnull()]
cc_dirty_rows = cc_all[cc_all["Contract Amount"].isnull()]

ncc_money_rows = ncc_all[ncc_all["Contract Amount $"].notnull()]

In [7]:
ncc_cleaned = ncc_money_rows[['Sole Source Reference','Client Division', 'Description','Vendor Name','Contract Amount $','Contract Date']]
ncc_cleaned = ncc_cleaned.rename(columns={"Sole Source Reference":"ref_id",
                                         "Client Division":"client_division",
                                         "Description":"description",
                                         "Vendor Name":"vendor",
                                         "Contract Amount $":"contract_value",
                                         "Contract Date":"date"})

cc_cleaned = cc_money_rows[['Call Number','Client Division/Contact', 'Description','Successful Bidder','Contract Amount','Date awarded']]
cc_cleaned = cc_cleaned.rename(columns={"Call Number":"ref_id",
                                         "Client Division/Contact":"client_division",
                                         "Description":"description",
                                         "Successful Bidder":"vendor",
                                         "Contract Amount":"contract_value",
                                         "Date awarded":"date"})

In [8]:
ncc_cleaned["type"] = "non-competitive"
cc_cleaned["type"] = "competitive"

all_contracts = pd.merge(ncc_cleaned, cc_cleaned, how="outer", on=["ref_id", 
                                                                  "client_division",
                                                                  "description",
                                                                  "vendor",
                                                                  "contract_value",
                                                                  "type",
                                                                  "date"])
# set index to brief id
all_contracts = all_contracts.set_index("ref_id")

# clean up NA values in contracts
to_NaN = [r'^\s*$', r'n\/a', r'N\/A', r'--', r'NA'] 

for i in to_NaN:
    all_contracts.contract_value = all_contracts.contract_value.replace(i, np.nan, regex=True)
    all_contracts.vendor = all_contracts.vendor.replace(i, np.nan, regex=True)

all_contracts.contract_value = all_contracts.contract_value.replace(r'Cancelled', np.nan, regex=False)
all_contracts = all_contracts[~all_contracts['contract_value'].isna()]
all_contracts['currency'] = "CAD"

# reformat to accommodate USD entry
all_contracts.contract_value = all_contracts.contract_value.replace(r'[\$,]', '', regex=True).str.strip()
usd_rows = all_contracts[all_contracts['contract_value'].str.contains('USD')]
all_contracts.at[2375,'currency'] = 'USD'
all_contracts['contract_value'] = all_contracts['contract_value'].str.replace(' USD','').str.strip()

# convert money column to float
all_contracts.contract_value = all_contracts.contract_value.astype('float')

# convert time column to year only
all_contracts['date'] = pd.DatetimeIndex(all_contracts['date']).year

# remove 2022 as it is incomplete
all_contracts = all_contracts[all_contracts["date"] != 2022]

all_contracts[all_contracts["type"] == "competitive"]
all_contracts.to_csv("all_contracts_02152022.csv")


all_contracts[all_contracts["client_division"] == "- Choose one -"]

client_division  \
ref_id                                      
3031373392                 - Choose one -   
Doc2852112229              - Choose one -   
Doc2962047211              - Choose one -   
Doc3133954872              - Choose one -   
Doc3143590185              - Choose one -   
2305234907                 - Choose one -   
Doc2906091374              - Choose one -   
Doc2871224079              - Choose one -   
3092946006                 - Choose one -   
2485564575(9118-20-5043)   - Choose one -   
24855648594(9118-20-5042)  - Choose one -   
2333265407 (9118-20-5037)  - Choose one -   
2457091244 (9120-20-5041)  - Choose one -   
2457091244(9120-20-5041)   - Choose one -   
2918995784                 - Choose one -   

                                                                                                                                        description  \
ref_id                                                                                                                                                
3031373392                 Midland Avenue – Road Reconstruction, Road Resurfacing, Watermain Replacement and Water Services from Sheppard Avenue Ea   
Doc2852112229                                                                                          Servicing of Solmetex Hg5 Amalgam Separators   
Doc2962047211                                                                                                              Dental Equipment Repairs   
Doc3133954872                                                                                                       Forensic software and hardware    
Doc3143590185                                                                                      SecureTransport Software and Maintenance Support   
2305234907                                                                                                                  Arboricultural Services   
Doc2906091374                                                                                              HDPE Pipes, Fittings and Fusion Services   
Doc2871224079                Supply and Delivery of all Skilled Labour, Materials and Parts to Perform Maintenance and Repairs to Hydraulic Systems   
3092946006                                                                                                        Processing Services of Yard Waste   
2485564575(9118-20-5043)                                                                                              Moss Park park Revitalization   
24855648594(9118-20-5042)                                                                                                    Architectural Services   
2333265407 (9118-20-5037)                                                                                              Landscape Architect Services   
2457091244 (9120-20-5041)                                                                                              engagement and communication   
2457091244(9120-20-5041)                                                                    Engagement & Communication Moss Park and John Innes CRC   
2918995784                                                                                                                    Professional Services   

                                                        vendor  \
ref_id                                                           
3031373392                                                 NaN   
Doc2852112229                         OCTAGON MEDICAL SERVICES   
Doc2962047211                                    K-Dental Inc.   
Doc3133954872                                              NaN   
Doc3143590185                               DUOLOGIK SOLUTIONS   
2305234907                 ONTARIO LINE CLEARING & TREE EXPERT   
Doc2906091374                       CAPITAL SEWER SERVICES INC   
Doc2871224079                           Action Hydraulics Ltd.   
3092946006                      

In [22]:
# fill in rows with incomplete 'client_division', based on ref_ID documents available here: https://wx.toronto.ca/inter/pmmd/callawards.nsf/postedawards?OpenView

corrections = [['3031373392', "Purchasing & Materials Management"],
['Doc2852112229', "Public Health"],
['Doc2962047211', "Public Health"],
['Doc3133954872 ', "Purchasing & Materials Management"],
['Doc3143590185', "Purchasing & Materials Management"],
['2305234907', "Parks, Forestry & Recreation"],
['Doc2906091374', "Solid Waste Management Services"],
['Doc2871224079', "Purchasing & Materials Management"],
['3092946006', "Solid Waste Management Services"],
               
['2485564575(9118-20-5043)', "Parks, Forestry & Recreation"],
['24855648594(9118-20-5042)', "Parks, Forestry & Recreation"],
['2333265407 (9118-20-5037)', "Parks, Forestry & Recreation"],
['2457091244 (9120-20-5041)', "Parks, Forestry & Recreation"],
['2918995784', "Parks, Forestry & Recreation"]]

for i in corrections:
    idx = i[0]
    all_contracts.at[idx,"client_division"] = i[1]

# correct incorrect funding total for ref_id = 2305234907, correct value: 40412989
all_contracts.at['2305234907', 'contract_value'] = 40412989

# also delete duplicate 

try:
  all_contracts = all_contracts.drop('2457091244(9120-20-5041)') 
except:
  print("not found, moving on")

# check again to make sure there are no new contracts to clean up

all_contracts[all_contracts["client_division"] == "- Choose one -"]
all_contracts

not found, moving on


client_division  \
ref_id                                                                                                      
2020-053                                                                 Facilities Design & Construction   
2020-053                                                                 Facilities Design & Construction   
11650                                                                                Real Estate Services   
11630                                                                                Real Estate Services   
11705                                                                                Real Estate Services   
1447141                                                                              Real Estate Services   
SR3019397335, WS3039800054                                                           Real Estate Services   
10948                                                                                      Fleet Services   
SR3207934799 WS3208158198                                                    Parks, Forestry & Recreation   
SR3142464022 WS3224934296                                                            Real Estate Services   
WS3292512713                                                                     Information & Technology   
SR3256144612 WS3263179013                                                                   Public Health   
WS3193821627                                                                   Emergency Medical Services   
WS3295878219                                                            Purchasing & Materials Management   
WS3298685904                                                            Purchasing & Materials Management   
WS3039603928                                                                          City Clerk's Office   
SR3257910074 WS3277783799                                                                   Toronto Water   
SR3248237805 WS3249957888                                               Purchasing & Materials Management   
WS3258581853                                                                                  311 Toronto   
WS3258581648                                                 Social Development, Finance & Administration   
WS3147851257 / SR3102852940                                               Solid Waste Management Services   
SR3156277231 WS3175301688                                    Social Development, Finance & Administration   
WS3224922022                                                                 Parks, Forestry & Recreation   
WS3234300405                                                                      Chief Financial Officer   
WS3256159154                                                                        Facilities Operations   
WS3261851128/ SR3251840475                                                        Transportation Services   
10773                                                                                      Fleet Services   
SR3228645491 WS3233133285                                                  Economic Development & Culture   
SR3229395569 WS3232638724                                                                   Public Health   
SR3188900537, WS3260143667                                                                  Fire Services   
SR3150216108, WS3179418894                                                                  Fire Services   
SR3103391993, WS3119475438                                                        Transportation Services   
WS3217065308                                                                               Fleet Services   
WS3216958572                                                                               Fleet Services   
WS3258581796                                                                                Toronto Water   
SR3183405739 WS3189908041                                

In [58]:
# filter 2021 contracts only
contracts_2021 = all_contracts[all_contracts["date"] == 2021] 

# group by client_division and summarize
by_division = pd.DataFrame(contracts_2021.groupby("client_division")["contract_value"].sum().sort_values(ascending=False))

# calculate the contract value total (100%)
total_spending = round(sum(by_division.contract_value),2)

# tally the division totals as percentages of total
by_division["percent_of_total"] = by_division.contract_value / total_spending
top_90percent = sum(by_division.percent_of_total[:13]) 

# convert to percentage
by_division["percent_of_total"] = by_division["percent_of_total"].apply(lambda x: "{:.2%}".format(x))


# next fix: combine 3 E&CS subcategories into one.




In [59]:
# find out which groups cover 90% of the money spent
by_division


contract_value  \
client_division                                                                
Engineering & Construction Services - Capital Works Delivery         2.6e+08   
Transportation Services                                              1.1e+08   
Parks, Forestry & Recreation                                         1.1e+08   
Real Estate Services                                                 9.9e+07   
Toronto Water                                                        8.0e+07   
Facilities Design & Construction                                     6.3e+07   
Information & Technology                                             6.3e+07   
Purchasing & Materials Management                                    5.2e+07   
Accounting Services                                                  4.4e+07   
Fleet Services                                                       4.1e+07   
Engineering & Construction Services - Engineering Services           3.9e+07   
Solid Waste Management Services                                      2.1e+07   
Social Development, Finance & Administration                         2.0e+07   
Fire Services                                                        1.9e+07   
Engineering & Construction Services - Engineering Review             1.3e+07   
Facilities Operations                                                1.1e+07   
Corporate Security                                                   1.0e+07   
Shelter, Support & Housing Administration                            8.3e+06   
Public Health                                                        5.6e+06   
Long-Term Care Homes & Services                                      3.8e+06   
Economic Development & Culture                                       2.7e+06   
Chief Financial Officer                                              2.6e+06   
City Manager's Office                                                2.1e+06   
Environment & Energy Office                                          1.9e+06   
City Clerk's Office                                                  1.8e+06   
Human Resources                                                      1.5e+06   
Emergency Medical Services                                           8.7e+05   
311 Toronto                                                          7.0e+05   
Pension, Payroll & Employee Benefits                                 6.9e+05   
Affordable Housing Office                                            4.5e+05   
Auditor General                                                      4.4e+05   
City Planning                                                        4.0e+05   
Municipal Licensing & Standards                                      3.7e+05   
Children’s Services                                                  2.8e+05   
Strategic Communications                                             1.9e+05   
Waterfront Secretariat                                               1.4e+05   
Court Services                                                       1.4e+05   
Legal Services                                                       5.2e+04   
Toronto Building                                                     3.0e+04   
Revenue Services                                                     1.0e+04   

                                                             percent_of_total  
client_division                                                                
Engineering & Construction Services - Capital Works Delivery           24.07%  
Transportation Services                                                10.08%  
Parks, Forestry & Recreation                                            9.68%  
Real Estate Services                                                    9.10%  
Toronto Water                                                           7.40%  
Facilities Design & Construction                                        5.82%  
Information & Technology                                     

In [ ]:
# bar chart splitting competitive and non-competitive contracts - group the last 10 or so into an inset bar that's split up with its own legend

fig1, ax1 = plt.subplots()

plt.show()

# 4 Image

# 5 Discussion